In [10]:
using Plots
using LaTeXStrings
using Colors, ColorSchemes
cs1 = ColorScheme(range(colorant"red", colorant"royalblue1", length=5));

const e_charge = 1.60217663E-19 
const r_e = 2.8179402895E-15
const mec2 = 510998.94999999995

using DelimitedFiles

using LazyGrids

# Lattice Parameters

In [2]:
rho = 1.5
gamma = 10000.0
phi_m = 0.2

beta = (1-1/gamma^2)^(1/2)
lamb = 0.01/rho

#sigma_z = 50e-6
#sigma_x = 50e-6

p0c = gamma * beta * mec2

#L0 = (24*sigma_z*rho^2)^(1/3)

5.109989474450051e9

# Beam Initialization

In [3]:
using Distributions, Random

# Fake Gaussian beam

Np = 5000000   # Number of macro-particles
Q = 5E-9       # Total charge in C

charges = ones(Np)*Q/Np;

bb = Array{Float64, 2}(undef, 6, Np);
Random.seed!(1234)

bb[1,1:Np] = rand(Normal(0, 50E-6), Np);
bb[2,1:Np] = rand(Normal(0, 50E-6), Np);
bb[3,1:Np] = rand(Normal(0, 50E-6), Np);
bb[4,1:Np] = rand(Normal(0, 50E-6), Np);
bb[5,1:Np] = rand(Normal(0, 50E-6), Np);
bb[6,1:Np] = rand(Normal(0, 1E-6), Np);

zmin = minimum(bb[5,:])
zmax = maximum(bb[5,:])
xmin = minimum(bb[1,:])
xmax = maximum(bb[1,:])

z_b = bb[5,:]
x_b = bb[1,:];

In [4]:
include("../core/kick2.jl")

csr2d_kick_calc_exit (generic function with 1 method)

# Wake grids computation (GPU required)
#### The computed wake grids from "csr2d_kick_calc_entrance" and "csr2d_kick_calc_exit"
#### have a unit of $1/m^2$.

### Entrance wake

In [65]:
phi = 0.05
nz=201
nx=101
nxp=301
M=8

dict_ent = csr2d_kick_calc_entrance(z_b, x_b, charges,
    gamma=gamma, rho=rho, phi=phi,
    nz=nz, nx=nx, nxp=nxp, M=M, reverse_bend=false);

 Applying charge deposition...
 Computing Case A+B wake grid(s) via GPU...
 22.981775 seconds (121 CPU allocations: 5.969 KiB)
 23.050536 seconds (128 CPU allocations: 6.203 KiB)
 Interpolating wake value at the particle positions...


In [98]:
surface(dict_ent["zv"]*1000, dict_ent["xv"]*1000, dict_ent["Ws_grid"]'/1e5, alpha = 0.6, camera=(20, 30))

surface!(title = "Entrance wake"*L" $Ws(z,x)$ at $\phi = 0.05$", xlabel = L"z(mm)", ylabel = L"x(mm)", zlabel = L"W_s~10^5/m^2")

surface!(xtickfont=font(10),ytickfont=font(10), ztickfont=font(12))
surface!(colorbar = false)

In [91]:
#contourf(dict_ent["zv"]*1000, dict_ent["xv"]*1000, dict_ent["Ws_grid"]')

#plot!(xlabel=L"$z(mm)$", ylabel=L"x(mm)", title="Entrance wake \n"*L" $Wx(z,x)$ at $\phi = 0.05$")
#plot!(xtickfont=font(12), ytickfont=font(12), guidefont=font(14), margin=3Plots.mm, legend=(0.75, 0.90), legendfontsize = 10)
#plot!(right_margin = 15Plots.mm)

In [100]:
surface(dict_ent["zv"]*1000, dict_ent["xv"]*1000, dict_ent["Wx_grid"]'/1e5, alpha = 0.6, camera=(20, 30))

surface!(title = "Entrance wake"*L" $Wx(z,x)$ at $\phi = 0.05$", xlabel = L"z(mm)", ylabel = L"x(mm)", zlabel = L"W_s~10^5/m^2")

surface!(xtickfont=font(10),ytickfont=font(10), ztickfont=font(12))
surface!(colorbar = false)

### Exit wake

In [81]:
phi_m = 0.02
lamb = 0.05
nz=201
nx=101
nxp=301
M=8

dict_exit = csr2d_kick_calc_exit(z_b, x_b, charges,
    gamma=gamma, rho=rho, phi_m=phi_m, lamb=lamb,
    nz=nz, nx=nx, nxp=nxp, M=M, reverse_bend=false)

 Applying charge deposition...
 Computing Case C+D+E wake grid(s) via GPU...
 37.800149 seconds (146 CPU allocations: 6.750 KiB)
 36.916922 seconds (140 CPU allocations: 6.609 KiB)
 Interpolating wake value at the particle positions...


Dict{String, AbstractArray{Float64}} with 7 entries:
  "zv"          => range(-0.000251101, stop=0.000272606, length=201)
  "ddelta_ds"   => [0.000328205, 0.000114821, 9.12652e-5, -9.11517e-5, 1.13085e…
  "Ws_grid"     => [-1.30975 -1.31594 … -1.89942 -1.88543; -0.13102 -0.125417 ……
  "lambda_grid" => [0.0 0.0 … 0.0 0.0; 0.0 0.0 … 0.0 0.0; … ; 0.0 0.0 … 0.0 0.0…
  "xv"          => range(-0.000247439, stop=0.000266661, length=101)
  "Wx_grid"     => [0.00187532 0.00185664 … -0.00250531 -0.00252118; 6.92794e-6…
  "dxp_ds"      => [1.06328e-5, 1.57157e-5, 1.5652e-5, 1.4903e-5, 1.54948e-5, 1…

In [94]:
#surface(dict_exit["zv"]*1000, dict_exit["xv"]*1000, dict_exit["Ws_grid"]'/1e5, alpha = 0.6, camera=(20, 30))

#surface!(title = "Exit wake \n"*L" $Ws(z,x)$ at $(\phi = 0.05, \lambda=0.05)$", xlabel = L"z(mm)", ylabel = L"x(mm)", zlabel = L"W_s~10^5/m^2")

#surface!(xtickfont=font(10),ytickfont=font(10), ztickfont=font(12), right_margin = 8Plots.mm)

In [92]:
#contourf(dict_exit["zv"]*1000, dict_exit["xv"]*1000, dict_exit["Ws_grid"]')

#plot!(xlabel=L"$z(mm)$", ylabel=L"x(mm)", title="Exit wake \n"*L" $Ws(z,x)$ $(\phi = 0.05, \lambda=0.05)$")
#plot!(xtickfont=font(12), ytickfont=font(12), guidefont=font(14), margin=3Plots.mm, legend=(0.75, 0.90), legendfontsize = 10)
#plot!(right_margin = 15Plots.mm)

In [93]:
#surface(dict_exit["zv"]*1000, dict_exit["xv"]*1000, dict_exit["Wx_grid"]'/1e5, alpha = 0.6, camera=(20, 30))

#surface!(title = "Exit wake \n"*L" $Wx(z,x)$ at $(\phi = 0.05, \lambda=0.05)$", xlabel = L"z(mm)", ylabel = L"x(mm)", zlabel = L"W_s~10^5/m^2")

#surface!(xtickfont=font(10),ytickfont=font(10), ztickfont=font(12), right_margin = 8Plots.mm)